In [ ]:
## CDO Command. RUn from the data directory
"""
for f in *.nc; do cdo -v -fldmean -ifthen ../../../UTILITY/MASKFILES/MASK_C01_SM.nc $f /home/midhunm/AI4KLIM/EXPMNTS/P02A_DeepDown_Generalization/ANALYSE/PLTDATA/FM02_QQPlot_Fldmean_Series/C01/$f; done
"""
pass

In [6]:
import os
import xarray as xr
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
from scipy.stats import linregress

# — Publication‐style fonts & sizes —
mpl.rcParams['font.family']    = 'serif'
mpl.rcParams['font.serif']     = ['DejaVu Serif']
mpl.rcParams['axes.titlesize'] = 16
mpl.rcParams['axes.labelsize'] = 14
mpl.rcParams['xtick.labelsize'] = 12
mpl.rcParams['ytick.labelsize'] = 12

# — data directory & model mapping —
DPATH = "/home/midhunm/AI4KLIM/EXPMNTS/P02A_DeepDown_Generalization/ANALYSE/PLTDATA/FM02_QQPlot_Fldmean_Series/C01"
data_dict = {
    'SRCNN'  : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m00_b13_c01_det00_out_2001_2023.nc',
    'FSRCNN' : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m01_b13_c01_det00_out_2001_2023.nc',
    'EDRN'   : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m02_b13_c01_det00_out_2001_2023.nc',
    'SRDRN'  : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m03_b13_c01_det00_out_2001_2023.nc',
    'U-NET'  : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m04_b13_c01_det00_out_2001_2023.nc',
    'AU-NET' : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m05_b13_c01_det00_out_2001_2023.nc',
    'U-GAN'  : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m07_b13_c01_det00_out_2001_2023.nc',
    'AU-GAN' : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m08_b13_c01_det00_out_2001_2023.nc',
    'DL-ENS' : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_end_b13_c01_det00_out_2001_2023.nc',
    'GAN-ENS': f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_eng_b13_c01_det00_out_2001_2023.nc',
}

# — load reference (observations) —
ref_path = os.path.join(DPATH, "p02a_ref_c01_2001_2023.nc")
ds_ref   = xr.open_dataset(ref_path)
ref_arr  = ds_ref["prec"].values   # ← change key if needed

# — common ticks for both axes —
ticks = np.arange(0, 37, 6)

# — set up a 3×4 figure, 300 dpi, shared axes —
fig, axes = plt.subplots(3, 4, figsize=(20, 16), dpi=500,
                         sharex=False, sharey=False)

# indices to fill: first two rows (0–7) and the two center slots of row 2 (9,10)
fill_ix = [0,1,2,3,4,5,6,7,9,10]

for ax, (name, path) in zip([axes[i] for i in fill_ix], list(data_dict.items())[:10]):

# for ax, (name, path) in zip([axes[i] for i in fill_ix], data_dict.items()):
    ds  = xr.open_dataset(path)
    arr = ds["prec"].values

    # co‐located pairs, mask out NaNs
    mask = (~np.isnan(ref_arr)) & (~np.isnan(arr))
    x = ref_arr[mask].ravel()
    y = arr[mask].ravel()

    # compute R²
    _, _, r_val, _, _ = linregress(x, y)
    r2 = r_val**2

    # plot data points
    ax.scatter(x, y, s=12, alpha=0.6, color='#1f77b4') # #0000FF

    # enforce square axes with fixed limits
    ax.set_xlim(0, 36)
    ax.set_ylim(0, 36)
    ax.set_aspect('equal', 'box')

    # set uniform ticks
    ax.set_xticks(ticks)
    ax.set_yticks(ticks)

    # 1:1 dashed line spanning full axis
    lim = ax.get_xlim()
    ax.plot(lim, lim, color='k', linestyle='--', linewidth=1) # #FF00FF

    # annotate R² in bottom-right
    ax.text(0.95, 0.05, f"$R^2 = {r2:.6f}$",
            transform=ax.transAxes, ha='right', va='bottom',
            fontsize=21,
            bbox=dict(boxstyle="round,pad=0.3", fc="white", ec="gray", alpha=0.7))

    # titles & labels
    ax.set_title(name, fontsize=26, fontweight='bold')
    ax.set_xlabel(r"Observed (mm day$^{-1}$)", fontsize=18)
    ax.set_ylabel(r"Downscaled (mm day$^{-1}$)", fontsize=18)
    ax.tick_params(labelsize=16)

# hide the two empty slots (leftmost and rightmost of bottom row)
axes[8].set_visible(False)
axes[11].set_visible(False)

# adjust subplot spacing
fig.tight_layout(pad=2.0)
fig.subplots_adjust(wspace=0.3, hspace=0.3)

save_dir = '/home/midhunm/AI4KLIM/EXPMNTS/P02A_DeepDown_Generalization/ANALYSE/RESULTS'
# plt.savefig(f'{save_dir}/Figure02.jpg', format = 'jpg', dpi=500, bbox_inches='tight',facecolor='w', edgecolor='w')
plt.show()


IndexError: index 3 is out of bounds for axis 0 with size 3

# Supplementary Figures

In [15]:
## CDO Process
""" 
#!/bin/bash

# Base directories
BASE_DIR="/home/midhunm/AI4KLIM/EXPMNTS/P02A_DeepDown_Generalization/ANALYSE"
MASK_DIR="${BASE_DIR}/UTILITY/MASKFILES"
INPUT_DIR="${BASE_DIR}/GENDATA/VALIDATION/MASTER"
OUTPUT_BASE="${BASE_DIR}/PLTDATA/FM02_QQPlot_Fldmean_Series"

# Loop over channels B01, B02, B03
for dom in B01 B02 B03; do
  maskfile="${MASK_DIR}/MASK_${dom}_SM.nc"
  outdir="${OUTPUT_BASE}/${dom}"
  mkdir -p "${outdir}"

  # Process all .nc files inside the subdirectory named “dom”
  for f in "${INPUT_DIR}/${dom}"/*.nc; do
    fname=$(basename "${f}")
    cdo -v -fldmean \
        -ifthen "${maskfile}" \
        "${f}" \
        "${outdir}/${fname}"
  done
done

"""
pass

## FigureSX_QQPlot_{B01/B02/B03}

In [7]:
def create_plot(dom):
    import os
    import xarray as xr
    import numpy as np
    import matplotlib.pyplot as plt
    import matplotlib as mpl
    from scipy.stats import linregress
    
    # — Publication‐style fonts & sizes —
    mpl.rcParams['font.family']    = 'serif'
    mpl.rcParams['font.serif']     = ['DejaVu Serif']
    mpl.rcParams['axes.titlesize'] = 16
    mpl.rcParams['axes.labelsize'] = 14
    mpl.rcParams['xtick.labelsize'] = 12
    mpl.rcParams['ytick.labelsize'] = 12
    
    # — data directory & model mapping —
    DPATH = f"/home/midhunm/AI4KLIM/EXPMNTS/P02A_DeepDown_Generalization/ANALYSE/PLTDATA/FM02_QQPlot_Fldmean_Series/{dom.upper()}"
    data_dict = {
        'SRCNN'  : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m00_b13_{dom}_det00_out_2015_2023.nc',
        'FSRCNN' : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m01_b13_{dom}_det00_out_2015_2023.nc',
        'EDRN'   : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m02_b13_{dom}_det00_out_2015_2023.nc',
        'SRDRN'  : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m03_b13_{dom}_det00_out_2015_2023.nc',
        'U-NET'  : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m04_b13_{dom}_det00_out_2015_2023.nc',
        'AU-NET' : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m05_b13_{dom}_det00_out_2015_2023.nc',
        'U-GAN'  : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m07_b13_{dom}_det00_out_2015_2023.nc',
        'AU-GAN' : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_m08_b13_{dom}_det00_out_2015_2023.nc',
        'DL-ENS' : f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_end_b13_{dom}_det00_out_2015_2023.nc',
        'GAN-ENS': f'{DPATH}/p02a_hp-b32-r7e4-wmae_e01_eng_b13_{dom}_det00_out_2015_2023.nc',
    }
    
    # — load reference (observations) —
    ref_path = os.path.join(DPATH, f"p02a_ref_{dom}_2015_2023.nc")
    ds_ref   = xr.open_dataset(ref_path)
    ref_arr  = ds_ref["prec"].values   # ← change key if needed
    
    # — common ticks for both axes —
    ticks = np.arange(0, 37, 6)
    
    # — set up a 3×4 figure, 300 dpi, shared axes —
    fig, axes = plt.subplots(3, 4, figsize=(20, 16), dpi=500,
                             sharex=False, sharey=False)
    axes = axes.flatten()
    
    # indices to fill: first two rows (0–7) and the two center slots of row 2 (9,10)
    fill_ix = [0,1,2,3,4,5,6,7,9,10]
    
    for ax, (name, path) in zip([axes[i] for i in fill_ix], data_dict.items()):
        ds  = xr.open_dataset(path)
        arr = ds["prec"].values
    
        # co‐located pairs, mask out NaNs
        mask = (~np.isnan(ref_arr)) & (~np.isnan(arr))
        x = ref_arr[mask].ravel()
        y = arr[mask].ravel()
    
        # compute R²
        _, _, r_val, _, _ = linregress(x, y)
        r2 = r_val**2
    
        # plot data points
        ax.scatter(x, y, s=12, alpha=0.6, color='#1f77b4') # #0000FF
    
        # enforce square axes with fixed limits
        ax.set_xlim(0, 36)
        ax.set_ylim(0, 36)
        ax.set_aspect('equal', 'box')
    
        # set uniform ticks
        ax.set_xticks(ticks)
        ax.set_yticks(ticks)
    
        # 1:1 dashed line spanning full axis
        lim = ax.get_xlim()
        ax.plot(lim, lim, color='k', linestyle='--', linewidth=1) # #FF00FF
    
        # annotate R² in bottom-right
        ax.text(0.95, 0.05, f"$R^2 = {r2:.6f}$",
                transform=ax.transAxes, ha='right', va='bottom',
                fontsize=21,
                bbox=dict(boxstyle="round,pad=0.3", fc="white", ec="gray", alpha=0.7))
    
        # titles & labels
        ax.set_title(name, fontsize=26, fontweight='bold')
        ax.set_xlabel(r"Observed (mm day$^{-1}$)", fontsize=18)
        ax.set_ylabel(r"Downscaled (mm day$^{-1}$)", fontsize=18)
        ax.tick_params(labelsize=16)
    
    # hide the two empty slots (leftmost and rightmost of bottom row)
    axes[8].set_visible(False)
    axes[11].set_visible(False)
    
    # adjust subplot spacing
    fig.tight_layout(pad=2.0)
    fig.subplots_adjust(wspace=0.3, hspace=0.3)
    
    save_dir = '/home/midhunm/AI4KLIM/EXPMNTS/P02A_DeepDown_Generalization/ANALYSE/RESULTS/SUPPINFO'
    plt.savefig(f'{save_dir}/FigureSX_QQPlot_{dom.upper()}.jpg', format = 'jpg', dpi=500, bbox_inches='tight',facecolor='w', edgecolor='w')
    plt.show()


## Generate the plots

In [2]:
for dom in ['b01', 'b02', 'b03']:
    create_plot(dom)